## Combining time-series and geospatial data

Elvis bidding combines of both time-series and geospatial data; much of this data is available from the BOEM https://www.data.boem.gov/ . Time series data includes lease holders over time, production data and others. Geospatial data includes lease-block locations, bathymetry, maps of infrastructure.

First steps in feature engineering is data visualization. In this notebook we explore Python/Jupyter solutions.

In [2]:
from os.path import dirname, join

import geopandas as gpd
import numpy as np
import pandas as pd

from elvis import datasets
from elvis.io.boem_from_file import (contours_to_geojson, 
                                    boem_lease_by_owner,
                                    get_current_leases,
                                    get_blocks_by_owner)
                                
from elvis.visualization.mapping import (bathymetry_underlay,
                                         create_map_from_geojson,
                                         colors as company_colors,
                                         geojson_underlay)


base_directory = dirname(datasets.__file__)

### BOEM lease block data
Load BOEM data, which is somewhat reduced (compared to freeze) selection of lease block information:
https://www.data.boem.gov/Leasing/LeaseAreaBlock/Default.aspx

This is just regular pandas loading and basic cleaning. There's a unique set of lease numbers, so we use that for indexing the dataframe.

Load BOEM data, this contains a record of "lease" owners, going back to the year 2000 (a very much reduced set compared to "freeze")
https://www.data.boem.gov/Leasing/LeaseOwner/Default.aspx

Some leases are owned by multiple parties, so we find such leases, flag them, extract the data as an independent "consortia_leases" data. The largest owner is attributed to the "lease", and we use the now unique lease numbers to index the dataframe.

## Current lease owner by company
Now we will go ahead and extract the current Equinor holdings, and then combine them with BOEM block maps to create a geospatial data we can visualize.

Combine the block data (extracted from GIS shape and other files), with the lease/owner information loaded above. Geopandas supports pandas style merge and joins. The 'geo_interface' member gives us an object that can be visualized.

In [3]:
equinor_leases = get_blocks_by_owner(base_directory, owner="equinor")
get_current_leases(equinor_leases, inplace=True);

### leaflet 
 
While geopandas does provide some basic mapping functions; we demonstrate leaflet. Which is a javascript library for making interactive maps. ipyleaflet and folium are python libraries that expose this functionality in the ipython/jupyter environment. 

Use this to render the current Equinor leases in the Gulf of Mexico (GOM).

In [4]:
bathymetry = contours_to_geojson(join(base_directory, 
                                      "Gulf_Bathymetric_Contours"),
                                      "contours_noaa_500m")

In [5]:
equinor_leases

BLOCKS_  BLOCKS_ID MMS_REGION MMS_PLAN_A PROT_NUMBE  \
Lease Number AREABLK                                                        
G36710       EB607       4323       4323          G       None    NG15-01   
G36711       EB648       4361       4361          G       None    NG15-01   
G36712       EB649       4362       4362          G       None    NG15-01   
G36713       EB650       4363       4363          G       None    NG15-01   
G36714       EB651       4364       4364          G       None    NG15-01   
...                       ...        ...        ...        ...        ...   
G36451       AT236      10070      10070          G       None    NG16-01   
G36782       MC758      23954      23954          G       None    NH16-10   
G36558       MC801      23994      23994          G       None    NH16-10   
G16661       MC941      24125      24125          G       None    NH16-10   
G24130       MC942      24126      24126          G       None    NH16-10   

                       PROT_APRV_ BLOCK_NUMB   BLK_FED_AP BLOCK_LAB AREA_CODE  \
Lease Number AREABLK                                                            
G36710       EB607    01-NOV-2000        607  01-NOV-2000       607        EB   
G36711       EB648    01-NOV-2000        648  01-NOV-2000       648        EB   
G36712       EB649    01-NOV-2000        649  01-NOV-2000       649        EB   
G36713       EB650    01-NOV-2000        650  01-NOV-2000       650        EB   
G36714       EB651    01-NOV-2000        651  01-NOV-2000       651        EB   
...                           ...        ...          ...       ...       ...   
G36451       AT236    01-NOV-2000        236  01-NOV-2000       236        AT   
G36782       MC758    01-NOV-2000        758  01-NOV-2000       758        MC   
G36558       MC801    01-NOV-2000        801  01-NOV-2000       801        MC   
G16661       MC941    01-NOV-2000        941  01-NOV-2000       941        MC   
G24130       MC942    01-NOV-2000        942  01-NOV-2000       942        MC   

                      ...  Status Code  Owner Aliquot Code Sn Lse Owner  \
Lease Number AREABLK  ...                                                 
G36710       EB607    ...            C                   1       295905   
G36711       EB648    ...            C                   1       295906   
G36712       EB649    ...            C                   1       295907   
G36713       EB650    ...            C                   1       295908   
G36714       EB651    ...            C                   1       295909   
...                   ...          ...                 ...          ...   
G36451       AT236    ...            C                   1       292876   
G36782       MC758    ...            C                   1       295982   
G36558       MC801    ...            C                   1       294637   
G16661       MC941    ...            C                   1       290221   
G24130       MC942    ...            C                   1       220223   

                     Approved Date MMS Start Date Asgn Term Date  \
Lease Number AREABLK                                               
G36710       EB607      2019-12-01     2018-08-06            NaN   
G36711       EB648      2019-12-01     2018-08-06            NaN   
G36712       EB649      2019-12-01     2018-08-06            NaN   
G36713       EB650      2019-12-01     2018-08-06            NaN   
G36714       EB651      2019-12-01     2018-08-06            NaN   
...                            ...            ...            ...   
G36451       AT236      2018-11-01     2018-08-06            NaN   
G36782       MC758      2019-11-01     2018-08-06            NaN   
G36558       MC801      2019-07-01     2018-08-06            NaN   
G16661       MC941      2017-10-17     2010-03-15            NaN   
G24130       MC942      2008-02-12     2008-01-18            NaN   

                     Owner Group Code Assignment Pct  Asgn Eff Date  Consortia  
Lease Number AREABLK    

In [6]:
equinor_leases.__geo_interface__

{'type': 'FeatureCollection',
 'features': [{'id': "('G36710', 'EB607')",
   'type': 'Feature',
   'properties': {'AREA_CODE': 'EB',
    'Approved Date': Timestamp('2019-12-01 00:00:00'),
    'Area Code': 'EB',
    'Asgn Eff Date': Timestamp('2019-12-01 00:00:00'),
    'Asgn Term Date': None,
    'Assignment Pct': 100.0,
    'BLK_FED_AP': '01-NOV-2000',
    'BLOCKS_': 4323,
    'BLOCKS_ID': 4323,
    'BLOCK_LAB': '607',
    'BLOCK_NUMB': '607',
    'Block Max Water Depth (meters)': 967,
    'Block Number': '607',
    'Company Name': 'equinorgulfofmexicollc',
    'Consortia': False,
    'Lease Effective Date': Timestamp('2019-12-01 00:00:00'),
    'Lease Expiration Date': None,
    'Lease Status Code': 'PRIMRY',
    'MMS Company Number': 2748,
    'MMS Start Date': Timestamp('2018-08-06 00:00:00'),
    'MMS_PLAN_A': None,
    'MMS_REGION': 'G',
    'Owner Aliquot Code': '1',
    'Owner Group Code': None,
    'PROT_APRV_': '01-NOV-2000',
    'PROT_NUMBE': 'NG15-01',
    'Shape_Area': 0.0

In [7]:
"STATOIL", "NORSK HYDRO", "SPINNACER"

('STATOIL', 'NORSK HYDRO', 'SPINNACER')

In [8]:
contours = geojson_underlay(bathymetry, 
                            name='bathymetry',
                            color='black',
                            weight=0.25)

create_map_from_geojson(equinor_leases.__geo_interface__,
                        color=company_colors["equinor"],
                        underlays=contours)

Map(center=[26.9792212296875, -91.87030927187499], controls=(ZoomControl(options=['position', 'zoom_in_text', …

In [9]:
pipelines = contours_to_geojson(join(base_directory, "ppl_arcs"),
                                "ppl_arcs")
# these are all of the types of pipelines
print(
np.unique(
    [f['properties']['ROW_NUMBER'] for f in pipelines['features']]))

['' 'ACID' 'AIR' 'BLGH' 'BLKG' 'BLKO' 'BLOH' 'CBLC' 'CBLP' 'CHEM' 'COND'
 'CSNG' 'FLG' 'G/C' 'G/O' 'G/OH' 'GAS' 'GASH' 'H2O' 'INJ' 'LIFT' 'METH'
 'O/W' 'OIL' 'OILH' 'SERV' 'SPLY' 'SPRE' 'SULF' 'TEST' 'UBEH' 'UMB' 'UMBC'
 'UMBE' 'UMBH']


In [10]:
oil_pipelines_json = contours_to_geojson(join(base_directory, "ppl_arcs"),
                                "ppl_arcs",
                                feature=('ROW_NUMBER',"oil"))
gas_pipelines_json = contours_to_geojson(join(base_directory, "ppl_arcs"),
                                "ppl_arcs", 
                                feature=('ROW_NUMBER',"gas"))
water_pipelines_json = \
    contours_to_geojson(join(base_directory, "ppl_arcs"),
                                "ppl_arcs", 
                                feature=('ROW_NUMBER',"h20"))

In [11]:
oil_pipelines_json

{'type': 'FeatureCollection',
 'bbox': (-97.36687695, 26.02142275, -82.57491100000001, 30.375578670312528),
 'features': [{'type': 'Feature',
   'properties': {'DeletionFlag': 6,
    'SEGMENT_NU': 65848,
    'SEG_LENGTH': 'ACT',
    'STATUS_COD': '08',
    'PPL_SIZE_C': 'G13496',
    'ROW_NUMBER': 'OIL',
    'PROD_CODE': 'R',
    'APRV_CODE': 'RENAISSANCE OFFSHORE LLC',
    'SDE_COMPAN': 0.203020610973},
   'geometry': {'type': 'LineString',
    'coordinates': ((-91.10145617031247, 28.506447979687493),
     (-91.09784242968749, 28.50646349062498),
     (-91.09521185937501, 28.506653909375018),
     (-91.0919399, 28.50692005000002),
     (-91.09057457031253, 28.506954620312513),
     (-91.08882712031249, 28.506996740625027),
     (-91.08749245000001, 28.507031329687493),
     (-91.08592597968749, 28.507081970312527),
     (-91.08439162031249, 28.50710787968751),
     (-91.08242417031249, 28.507138459375028),
     (-91.08134692968753, 28.507151520312505),
     (-91.07961652031253, 28.507

In [12]:
oil = geojson_underlay(oil_pipelines_json, 
                       name='oil',
                       color='black',
                       weight=0.25)
gas = geojson_underlay(gas_pipelines_json, 
                       name='gas',                       
                       color='green',
                       weight=0.25)
water = geojson_underlay(water_pipelines_json, 
                       name='water',                                                
                       color='blue',
                       weight=0.25)

create_map_from_geojson(equinor_leases.__geo_interface__,
                        color=company_colors["equinor"],
                        underlays=[oil, gas, water])

Map(center=[26.9792212296875, -91.87030927187499], controls=(ZoomControl(options=['position', 'zoom_in_text', …

In [13]:
high_res_bathymetry = bathymetry_underlay()

create_map_from_geojson(equinor_leases.__geo_interface__,
                        color=company_colors["equinor"],
                        underlays=[high_res_bathymetry, oil, gas, water],
                        control=True)

Map(center=[26.9792212296875, -91.87030927187499], controls=(ZoomControl(options=['position', 'zoom_in_text', …